# ***Seattle Energy Benchmarking***

## *Online version*

An online version of this notebook is available on *Google Colab* at the following address: 

https://colab.research.google.com/drive/1vHosA0ECtpsLkb9CG_D_Vn1nAXlrzJzq?usp=sharing 

# ***- 1 -*** About this project

## *A -* Introduction

In this project, we are working for the city of Seattle and with its open data. The goal is to facilitate the building energy statement generation for the non-residential buildings.

Complex and complete energy statements have been made by the city, but they represent a big effort and our task is to simplify the process using our Data Science skills.

In this project, we have multiple objectives:
* Predict the energy consumption and green house gas emissions of the buildings,
* Investigate the EnergyStar score and determinate if it is relevant for the greenhouse gas emissions predictions.

In order to fullfill these objectives:
* We are going to implement custom Sklearn transformers to create a pipeline for our data.
* Then, we train and evaluate multiple machine learning models to select the best estimator for our problematic.

The original dataset can be found at the following address:

https://www.kaggle.com/city-of-seattle/sea-building-energy-benchmarking/code

## *B -* How to read this project

This project is divided into 2 notebooks.
Each notebook is organized in chapters:


**Common chapters**
* ***-1 -*** **About this project** is *what you are reading now*. This is the *README*.
* ***0 -*** **Environment**: sets up the necessary environment to run this notebook. In this part, we will also develop the toolbox to automate the exploration of the dataset. *Disclaimer: This part is not really about Data Science, but more about code and automatized processing. It is not necessary to read this part unless you have a good knowledge of python and are interested on how I delevelopped these functions. Fee free to skip it.*
* ***+1 -*** **Conclusion**: The notebooks conclusion.

***P3.1 -*** **Exploration** (*first notebook*)
* ***1 -*** **Cleaning and Exploration**: main dataset characteristics and basic data cleaning.
* ***2 -*** **Going Deeper**: characteristics of the main features of the dataset.

***P3.2 -*** **Feature Enginering** (*second notebook*)
* ***3 -*** **Feature Engineering**: creation of the preprocessing pipeline.
* ***4 -*** **Energy Use Prediction**: prediction of the energy use per building.
* ***5 -*** **Greenhouse Gas Emissions Prediction**: prediction of the greenhouse gas emissions and evaluation of the impact of the *EnergyStarScore* feature.

# ***0 -*** **Environment**

## *A -* Importing Libraries

Let's import the libraries that will be used in this project.

In [ ]:
import pandas as pd
import numpy as np
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler, FunctionTransformer, QuantileTransformer, MinMaxScaler
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
from matplotlib.collections import LineCollection
import json
import folium
import folium.plugins
import geopy.distance

## *B -* Utilities

In [ ]:
plt.rcParams["figure.figsize"] = (14,12)
template = 'plotly_dark'

### *a -* Dataset Versioning

I have developped the **Dataset()** class during this project as a simple dataset versioning tool.

*You can skip this part in you are not interested in code.*

In [ ]:
def get_num(dataframe:pd.DataFrame):

  return dataframe.select_dtypes([int,float])


def get_cat(dataframe:pd.DataFrame):

  return dataframe.select_dtypes(object)


def get_feat(dataframe:pd.DataFrame, starts_with:str, inverse=False):

  # or tuple of strings
  if inverse == True:
    return [feature for feature in dataframe.columns if feature.endswith(starts_with)]
  else:
    return [feature for feature in dataframe.columns if feature.startswith(starts_with)]


def gen_feat(dataframe:pd.DataFrame, prefix:str, inverse=False):

    if inverse == True:
      return [f'{prefix}{feature}' for feature in dataframe.columns]
    else:
      return [f'{feature}{prefix}' for feature in dataframe.columns]

  
class Dataset():


  def __init__(self, dataframe:pd.DataFrame):

    init_name = 'original'
    self.versions_index = {init_name:0}
    self.versions = {0:self.dict_constructor(dataframe=dataframe, step=init_name, index=0)}
    self.current_version = 0

    print(f'Version {self.current_version}: "{init_name}" initialized') 


  def last_index(self):

    return list(self.versions_index.values())[-1]


  def add_index(self, step, index):

    if step in list(self.versions_index.keys()) or step=='current':
      print('\nKey already in index, choose another key.\n')
      return False

    else:
      self.versions_index[step] = index
      return True


  def dict_constructor(self, dataframe, step, index):

    if index == 0:
      samples_diff = dataframe.shape[0]
      features_diff = dataframe.shape[1]
      index_diff = dataframe.index
      columns_diff = dataframe.columns

    else:
      last_version = self.versions.get(index-1)
      samples_diff = last_version.get('samples') - dataframe.shape[0]
      features_diff = last_version.get('features') - dataframe.shape[1]
      index_diff = last_version.get('index').difference(dataframe.index)
      columns_diff = last_version.get('columns').difference(dataframe.columns)

    dataframe_dict = {
      'name': step,
      'dataframe': dataframe,
      'samples': dataframe.shape[0],
      'samples_diff': samples_diff,
      'features': dataframe.shape[1],
      'features_diff': features_diff,
      'index': dataframe.index,
      'index_diff': index_diff,
      'columns': dataframe.columns,
      'columns_diff': columns_diff
    }

    return dataframe_dict


  def save_version(self, updated_dataframe:pd.DataFrame, step:str):

    next_version = self.last_index() + 1
    key_pass = self.add_index(step=step, index=next_version)
    if key_pass == True:
      self.versions[next_version] = self.dict_constructor(dataframe=updated_dataframe, step=step, index=next_version)
      self.current_version = next_version
      print(f'\nVersion {next_version}: "{step}" saved\n')    


  def parse_step(self, step):

    if type(step) == str:
      version_index = self.versions_index.get(step)
      version_name = step
    if type(step) == int:
      version_index = step
      version_name = self.versions.get(version_index).get('name')
    return version_index, version_name


  def get_version(self, step):

    version_index, version_name = self.parse_step(step)

    return self.versions.get(version_index)


  def delete_version(self, step):

    version_index, version_name = self.parse_step(step)
    del self.versions_index[version_name]
    del self.versions[version_index]

    print(f'\nVersion {version_index}: "{version_name}" deleted\n')


  def pull_features(self, features, step=0):

    return self.get_version(self.current_version).get('dataframe').join(self.get_version(step).get('dataframe')[features], how='inner')


  def get(self, item='dataframe', step='current'):

    if step == 'current': version = self.versions.get(self.current_version)
    elif step == 'latter': version = self.versions.get(self.current_version-1)
    else: version = self.get_version(step)

    try: 
      item = version.get(item)
      return item
    except KeyError: 
      print('\nKey error, try generating the item first.\n')


  def num_report(self, fig_fill_min=100):

    dataframe = self.get()

    samples = dataframe.shape[0]
    report = dataframe.select_dtypes([int, float, 'datetime']).describe().transpose()
    report['fill_%'] = ((report['count'] / samples) * 100).astype(float).round(2)
    report['nans'] = dataframe.isna().sum()
    report['nans_%'] = ((report['nans'] / samples) * 100).astype(float).round(2)

    for i in report.index:
      zeroes_count = dataframe[i][dataframe[i] == 0].shape[0]
      report.loc[i, 'zeroes'] = zeroes_count
      report.loc[i, 'zeroes_%'] = round(((zeroes_count / samples) * 100), 2)

    report = report[['count', 'fill_%', 'nans', 'nans_%','zeroes', 'zeroes_%','mean', 'std', 'min', '25%', '50%', '75%', 'max']]
    report = report.sort_values(by='count', ascending=False).rename_axis(mapper='feature', axis=0)
    report_df = report[report['fill_%'] >= fig_fill_min][['fill_%', 'nans_%', 'zeroes_%']].transpose()
    report_fig = go.Figure(data=[go.Bar(name=str(report_df.index[index]), x=list(report_df.columns.values), y=list(report_df.iloc[index,:].values)) for index in range(report_df.shape[0])])

    if fig_fill_min == 0: title = 'numerical features characteristics'
    else: title = f'numerical features characteristics (fill >= {fig_fill_min}%: {report_df.shape[1]})'

    report_fig.update_layout(template=template,title=title)
    report_fig.show()

    self.versions[self.current_version]['numericals'] = report


  def cat_report(self, fig_fill_min=100):

    dataframe = self.get()

    samples = dataframe.shape[0]
    report = dataframe.select_dtypes('object').describe().transpose()
    report['fill_%'] = ((report['count'] / samples) * 100).astype(float).round(2)
    report['uniques_%'] = ((report['unique'] / samples) * 100).astype(float).round(2)
    report['nans'] = dataframe.isna().sum()
    report['nans_%'] = ((report['nans'] / samples) * 100).astype(float).round(2)
    report = report[['count', 'fill_%', 'unique', 'uniques_%', 'nans', 'nans_%', 'top', 'freq']]
    report = report.sort_values(by='count', ascending=False).rename_axis(mapper='feature', axis=0)
    report_df = report[report['fill_%'] >= fig_fill_min][['fill_%', 'nans_%', 'uniques_%']].transpose()
    report_fig = go.Figure(data=[go.Bar(name=str(report_df.index[index]), x=list(report_df.columns.values), y=list(report_df.iloc[index,:].values)) for index in range(report_df.shape[0])])

    if fig_fill_min == 0: title = 'categorical features characteristics'
    else: title = f'categorical features characteristics (fill >= {fig_fill_min}%: {report_df.shape[1]})'

    report_fig.update_layout(template=template,title=title)
    report_fig.show()

    self.versions[self.current_version]['categoricals'] = report


  def report(self, fig_fill_min=0):

    dataframe = self.get()

    if self.current_version > 0:

      version_old = self.versions.get(self.current_version-1)
      samples_old, features_old = version_old.get('samples'), version_old.get('features')
      samples_diff = samples_old - dataframe.shape[0]
      samples_percent = round((samples_diff / samples_old) * 100, 2)
      features_diff = features_old - dataframe.shape[1]
      features_percent = round((features_diff / features_old) * 100, 2)
      print(f'\nSamples dropped: {samples_diff}/{samples_old} ({samples_percent}%)\nFeatures dropped: {features_diff}/{features_old} ({features_percent}%)\n')

    # fig 1
    num_df = self.num_report(fig_fill_min)
    # fig 2
    cat_df = self.cat_report(fig_fill_min)

  
  def help(self):

    print('This is the help.')


### *b -* Data Summarization

These are wrapper functions that I have developed to explore the dataset.

The dataset has close to 2 millions rows. In order to process this data in an efficient way, we will need to make use of the pandas *vectorization*, or risk to run into performance issues.

*You can skip this part in you are not interested in code.*

In [ ]:
def shape_diff(shape_0,shape_1):
  dropped_samples = shape_0[0] - shape_1[0]
  dropped_features = shape_0[1] - shape_1[1]
  if dropped_samples > 0:
    print(f'Dropped samples: {dropped_samples}')
  if dropped_features > 0:
    print(f'Dropped features: {dropped_features}')


def scatter_matrix(dataframe:pd.DataFrame, third_dimension='', title='Scatter matrix of the dataset'):

    dataframe = get_num(dataframe)

    if len(third_dimension) > 0:

      fig = px.scatter_matrix(dataframe,
        dimensions=dataframe.columns,
        color=third_dimension,#, symbol="nutriscore_grade",
        title=title,
        labels={col:col.replace('_', ' ') for col in dataframe.columns}) # remove underscore

    else:

      fig = px.scatter_matrix(dataframe,
        dimensions=dataframe.columns,
        title=title,
        labels={col:col.replace('_', ' ') for col in dataframe.columns}) # remove underscore

    fig.update_traces(diagonal_visible=True)
    fig.update_layout(template=template,height=1000)
    fig.show()


def split_by_corr(dataframe:pd.DataFrame, max_corr=0.5):

  cor_matrix = get_num(dataframe).corr().abs()
  upper_tri = cor_matrix.where(np.triu(np.ones(cor_matrix.shape),k=1).astype(np.bool))

  high_corr = [column for column in upper_tri.columns if any(upper_tri[column] >= max_corr)]
  low_corr = list(set(dataframe.columns).difference(set(high_corr)))

  return low_corr, high_corr


def dual_scatter_matrix(dataframe:pd.DataFrame, third_dimension='', split_corr=0.5):

  if len(third_dimension) > 0:

    third_dimension_values = dataframe[third_dimension]
    dataframe = dataframe.drop(third_dimension, axis=1)

  if split_corr != 0:

    title_low = f'Scatter matrix of the dataset (correlations: <{(split_corr * 100)}%)'
    title_high = f'Scatter matrix of the dataset (correlations: >{split_corr * 100}%)'
    low_corr, high_corr = split_by_corr(dataframe, split_corr)

    for dataframe_subset, title in zip([dataframe[low_corr],dataframe[high_corr]],[title_low,title_high]):
      
      dataframe_subset[third_dimension] = third_dimension_values
      scatter_matrix(dataframe_subset,third_dimension,title)
  
  else:

    scatter_matrix(dataframe,third_dimension)


def plot_distributions(dataframe:pd.DataFrame, n_quantiles=1000, bin_size=500):

  for feature in dataframe.select_dtypes([int,float]).columns:

    original = dataframe[feature].values

    log_transformer = FunctionTransformer(lambda value: np.log(value + 1), inverse_func = lambda value: np.exp(value - 1), check_inverse = True)
    logged = log_transformer.transform(original).flatten()

    quantile_transformer = QuantileTransformer(output_distribution='normal', n_quantiles=n_quantiles)
    normalized = quantile_transformer.fit_transform(original.reshape(-1,1)).flatten()

    subplots = {'Original':original,'Logged':logged, f'QuantileTransformer (n_quantiles={n_quantiles})':normalized}

    bin_original, bin_logged, bin_normalized = (original.max() - original.min()) / bin_size, (logged.max() - logged.min()) / bin_size, (normalized.max() - normalized.min()) / bin_size
    distplot = ff.create_distplot([original,logged,normalized], group_labels=[feature,'Log','Normalized'], bin_size=[bin_original, bin_logged, bin_normalized], curve_type='normal', show_rug=False)

    fig = make_subplots(
      rows=1, cols=3,
      specs=[[{}, {}, {}]],
      subplot_titles=list(subplots.keys()))
    
    histogram_dict, scatter_dict = dict(enumerate(distplot['data'][:3])), dict(enumerate(distplot['data'][3:]))

    for column, title in enumerate(subplots.keys()):

      values = pd.Series(subplots[title])
      skewness, kurtosis = round(values.skew(),2), round(values.kurtosis(),2)
      legend = f'Skewness: {skewness} - Kurtosis: {kurtosis}'

      fig.add_trace(go.Histogram(histogram_dict[column]), row=1, col=column + 1)
      fig.add_trace(go.Scatter(scatter_dict[column]), row=1, col=column + 1)
      fig.update_xaxes(title_text=legend, row=1, col=column + 1)

    fig.update_xaxes(type='log',row=1, col=2)
    fig.update_layout(template=template, showlegend=False, title_text=feature)
    fig.show()


def plot_series_vs(primary:pd.Series, secondary:pd.Series, X_param:pd.Series, X_type='linear'):

  fig = make_subplots(specs=[[{"secondary_y": True}]])

  for metric in [primary] + [secondary]:
    if len(metric) > 0:
      metric_format = f'mean_test_{metric}'
      min_max_scaler = MinMaxScaler()
      values = metric.values
      scaled_values = min_max_scaler.fit_transform(values.reshape(-1,1))
      values_flat = values.flatten()
      values_range = [values_flat.min(),values_flat.max()]
      if metric.name == primary.name:
        secondary_axis = False
        fig.update_yaxes(title_text=primary.name,secondary_y=False,range=values_range)
      else:
        secondary_axis = True
        fig.update_yaxes(title_text=secondary.name,secondary_y=True,range=values_range)
      fig.add_trace(go.Scatter(x=X_param.values, y=values_flat,
                        mode='markers',
                        name= metric.name
                        ),secondary_y = secondary_axis)
      
    else:
      continue

  fig.update_xaxes(type=X_type, title_text=f'{X_param.name} ({X_type})', exponentformat="e")
  fig.update_layout(template=template, title=f'Scaled {primary.name} vs. {secondary.name} by {X_param.name}')
  fig.show()


def knn_optimizer(model, X_train:pd.DataFrame, y_train:pd.DataFrame, X_val:pd.DataFrame, y_val:pd.DataFrame, metric, range=range(1,10)):  

  best_id, best_neighbors, best_score = 0, 0, None

  for id, neighbors in enumerate(range):

    knn = model(n_neighbors=neighbors)
    knn.fit(X_train, y_train)
    predictions = knn.predict(X_val)

    if metric == 'accuracy':

      score = accuracy_score(y_val, predictions)
      score = round(score * 100, 2)
      print(f'\nPass {id}: {neighbors} neighbor(s), {metric}: {score}')

      if best_score is None or score > best_score:
        best_neighbors, best_score, best_id = neighbors, score, id
      
    if metric == 'MSE':

      score = mean_squared_error(y_val, predictions)
      score = round(score, 2)
      print(f'\nPass {id}: {neighbors} neighbor(s), {metric}: {score}')

      if best_score is None or score < best_score:
        best_neighbors, best_score, best_id = neighbors, score, id

  print(f'\nBest pass {best_id}: {best_neighbors} neighbor(s), {metric}: {best_score}')
  
  return model(n_neighbors=best_neighbors).fit(X_train, y_train)


def eta_squared(x,y):
    moyenne_y = y.mean()
    classes = []
    for classe in x.unique():
        yi_classe = y[x==classe]
        classes.append({'ni': len(yi_classe),
                        'moyenne_classe': yi_classe.mean()})
    SCT = sum([(yj-moyenne_y)**2 for yj in y])
    SCE = sum([c['ni']*(c['moyenne_classe']-moyenne_y)**2 for c in classes])
    return SCE/SCT


def anova(dataframe:pd.DataFrame,by:str):

  dataframe_eta = dataframe.select_dtypes([int,float])
  dataframe_eta = pd.DataFrame(QuantileTransformer().fit_transform(dataframe_eta), columns=dataframe_eta.columns, index=dataframe_eta.index)
  dataframe_eta.loc['Eta²'] = dataframe_eta.apply(lambda column: eta_squared(dataframe[by], column.values), axis=0)
  dataframe_eta = pd.DataFrame(dataframe_eta.loc['Eta²',:]).rename_axis('Feature',axis=0).reset_index()
  fig = px.bar(dataframe_eta, x='Feature', y='Eta²', title=f'{by} Anova (on the normalized distributions)', template=template)
  fig.show()


def dist_plot(dataframe:pd.DataFrame, feature:str, by=None, bin_size=0.5):

  subsets = list()
  labels = list()
  if by is not None:
    labels = list(set(dataframe[by].values))
    labels.sort()
    for filter in labels:
      subsets.append(dataframe[dataframe[by]==filter][feature].values)
  else:
    labels = [feature]
    subsets = [dataframe[feature].values]

  fig = ff.create_distplot(subsets, group_labels=labels, bin_size=bin_size,
                          curve_type='normal', show_rug=False
                          )
  fig.update_layout(template=template,title_text=f'{feature} vs normal distribution', height=750)
  fig.show()


def heatmap(matrix:pd.DataFrame, title='', extra=None):

  if extra is not None:
    extra = extra.values
  fig = ff.create_annotated_heatmap(matrix.values, x=matrix.columns.to_list(), y=matrix.index.to_list(), annotation_text=extra)
  fig.update_layout(template=template,title=title)
  fig.show()


def pie_plot(dataframe:pd.DataFrame, feature:str):

  fig_df = pd.DataFrame(pd.Series((','.join(dataframe[feature].astype(str).to_list())).split(',')).value_counts(), columns=['population']).rename_axis(mapper='tag', axis=0)
  fig = px.pie(fig_df.reset_index(), names='tag', values='population', title=f'{feature} population')
  fig.update_layout(template=template)
  fig.show()


def bar_plot(dataframe:pd.DataFrame, feature:str):

  fig_df = pd.DataFrame(pd.Series((','.join(dataframe[feature].astype(str).to_list())).split(',')).value_counts(), columns=['population']).rename_axis(mapper='tag', axis=0)
  fig = px.bar(fig_df.reset_index(), x='tag', y='population', title=f'{feature} population')
  fig.update_layout(template=template)
  fig.show()


def box_plots(x_data,y_data, outliers=False):

  flattened_y = np.hstack(np.array(y_data))
  max_min = np.max(flattened_y) - np.hstack(flattened_y).min()
  range = int('1' + len(str(max_min)) * '0')
  dtick = max_min // range
  colors = ['rgba(93, 164, 214, 0.5)', 'rgba(255, 144, 14, 0.5)', 'rgba(44, 160, 101, 0.5)',
            'rgba(255, 65, 54, 0.5)', 'rgba(207, 114, 255, 0.5)', 'rgba(127, 96, 0, 0.5)']
      
  fig = go.Figure()

  for xd, yd, cls in zip(x_data, y_data, colors):
          fig.add_trace(go.Box(
              y=yd,
              name=xd,
              boxpoints=outliers,
              jitter=0.5,
              whiskerwidth=0.2,
              fillcolor=cls,
              marker_size=1,
              line_width=1)
          )

  fig.update_layout(
      yaxis=dict(
          autorange=True,
          showgrid=True,
          zeroline=True,
          dtick=dtick,
          gridcolor='rgb(255, 255, 255)',
          gridwidth=1,
          zerolinecolor='rgb(255, 255, 255)',
          zerolinewidth=2,
      ),
      margin=dict(
          l=40,
          r=30,
          b=80,
          t=100,
      ),
      paper_bgcolor='rgb(243, 243, 243)',
      plot_bgcolor='rgb(243, 243, 243)',
      showlegend=False
  )

  return fig

  
def batch_box_plots(dataframe:pd.DataFrame, by=None, title='', outliers=False):

  dataframe_num = dataframe.select_dtypes([int,float])

  if by is None:
    x_data = dataframe_num.columns.to_list()
    y_data = np.array([dataframe_num[feature].values for feature in x_data])
    fig = go.Figure()

    fig = box_plots(x_data,y_data,outliers)
    fig.update_layout(title=title)
    fig.show()

  else:

    for feature in dataframe_num.columns:

      filters = list(set(dataframe[by].values))
      filters.sort()
      x_data = filters
      y_data = [dataframe[dataframe[by]==filter][feature].values for filter in filters]

      fig = box_plots(x_data,y_data,outliers)
      fig_title = f'Box plots by {by} ({feature})'
      fig.update_layout(title=fig_title)
      fig.show()


def dist_plot(dataframe:pd.DataFrame, feature:str, by:str, bin_size=1):

  subsets = list()
  labels = list(set(dataframe[by].values))
  for filter in labels:
    subsets.append(dataframe[dataframe[by]==filter][feature].values)
  fig = ff.create_distplot(subsets, group_labels=labels, bin_size=bin_size,
                          curve_type='normal', show_rug=False)

  fig.update_layout(template=template,title_text=f'{feature} vs normal distribution', height=750)
  fig.show()


def sum_dtypes(dataframe:pd.DataFrame):

  dtypes = dataframe.dtypes.value_counts()
  dtypes.index = dtypes.index.astype(str)
  dtypes = pd.DataFrame(data=dtypes, columns=['population']).rename_axis(mapper='dtype', axis=0)
  dtypes_fig = px.pie(dtypes.reset_index(), names='dtype', values='population', title="dtypes repartition")
  dtypes_fig.update_layout(template=template)
  dtypes_fig.show()

  return dtypes


def sum_nans(dataframe:pd.DataFrame):

  samples, features = dataframe.shape[0], dataframe.shape[1]
  nans = dataframe.isna().sum()
  nans = pd.DataFrame(data=nans, columns=['nans']).rename_axis(mapper='feature', axis=0).sort_values(by='nans', ascending=False)
  nans['nans_%'] = ((nans['nans'] / dataframe.shape[0]) * 100).round(2)

  return nans


def sum_uniques(dataframe:pd.DataFrame):

  samples, features = dataframe.shape[0], dataframe.shape[1]
  uniques = dataframe.nunique()
  uniques = pd.DataFrame(data=uniques, columns=['uniques']).rename_axis(mapper='feature', axis=0).sort_values(by='uniques', ascending=False)
  uniques['uniques_%'] = ((uniques['uniques'] / dataframe.shape[0]) * 100).round(2)

  return uniques


def join(series):

  return series.to_list()


def sample(*series):

  df = pd.DataFrame()
  
  for serie in series:
    if serie.name in df.columns:
      suffix = '_1'
    else:
      suffix = ''
    uniques = serie.unique()
    if len(uniques) >= 10:
      sample = pd.Series(uniques).sample(10)
      df[f'{serie.name}{suffix}'] = sample.values
    else:
      sample = serie.sample(10)
      df[f'{serie.name}{suffix}'] = sample.values
    df[f'{serie.name}_index{suffix}'] = sample.index
  
  df = df.reset_index().drop('index', axis=1).rename_axis(mapper='sample', axis=0)
  
  return df


def filter_tags(dataframe:pd.DataFrame, filters:dict):

  dataframe_features = dataframe.columns.tolist()
  features_df = pd.DataFrame(dataframe.columns, columns=['features'], index=dataframe.columns).rename_axis(mapper='index', axis=0)
  features_df['dtype'] = dataframe.dtypes.astype(str).values
  features_df['cat'] = features_df['dtype'].str.contains('object')
  features_df['num'] = features_df['dtype'].str.contains('float64')
  features_df['startswith'] = features_df['features'].str.split('_').str[0]
  features_df['splits'] = features_df['features'].str.count('_')
  features_df['processed'] = features_df['features']

  for filter in filters:
    if filter == 'endswith':
      for tag in filters[filter]:
        features_df[f'...{tag}'] = features_df['features'].str.endswith(tag)
        features_df['processed'] = features_df['processed'].str.replace(tag + r'$', '')

  filters_endswith = {f'...{filter}':sum for filter in filters['endswith']}
  misc = {feature:sum for feature in ['cat','num']}
  # dataframe qui filtre les startwith pat tag pour trouver les noms uniques
  features_filtered_df = features_df.groupby(by='startswith').agg({**misc, **filters_endswith, **{'splits': max, 'features': join, 'processed':join}}).rename_axis(mapper='index', axis=0)
  features_filtered_df['startswith_filtered'] = features_filtered_df.index
  features_filtered_df['total'] = features_filtered_df['cat'] + features_filtered_df['num']
  features_filtered_df_cols = features_filtered_df.columns.to_list()
  features_filtered_df = features_filtered_df[[features_filtered_df_cols[-1]]+features_filtered_df_cols[:-1]]
  features_filtered_df['processed'] = features_filtered_df['processed'].apply(lambda cell: set(cell))
  features_filtered_df = features_filtered_df.sort_values(by='splits', ascending=False)
  # recroisement avec la liste de features du dataframe
  features_names = [name for names in features_filtered_df['processed'].to_list() for name in names]
  features_final = list()

  for filter in filters:
    if filter == 'endswith':
      for feature_name in features_names:
          for tag in filters[filter] + ['']:
            temp_feature_name = f'{feature_name}{tag}'
            if temp_feature_name in dataframe_features:
              features_final.append(temp_feature_name)
              break

  print(f'\n{len(dataframe_features) - len(features_final)} features dropped\n')

  return features_final, features_filtered_df.drop('startswith_filtered', axis=1)


def filter_cat_feature(dataframe:pd.DataFrame, by:str, minimum_coverage=100):

  #filter top features with minimum cov and plot top features and others
  feature = dataframe[by].astype(str)
  features_df = pd.DataFrame(pd.Series((','.join(feature.to_list())).split(',')).value_counts(), columns=['population']).rename_axis(mapper='tag', axis=0)
  features_df['population_%'] = round((features_df['population'] / features_df['population'].values.sum()) * 100, 2)
  features_df['cumulative_uniques_%'] = features_df['population_%'].values.cumsum()
  features_n = features_df.shape[0]
  top_features_n = 0
  
  if minimum_coverage == 100:
    top_features = features_df.index.to_list()
    others = None

  else:
    for feature_index, coverage in enumerate(features_df['cumulative_uniques_%'].to_list()):
      if coverage >= minimum_coverage:
        top_features_n = feature_index +1
        break
    top_features = features_df.index.to_list()[:top_features_n]
    others = features_df[top_features_n:]
    
  top_features_df = features_df

  if others is not None:
    top_features_df = features_df.copy().head(top_features_n)
    top_features_df.loc['others',:] = [others['population'].sum(), others['population_%'].sum(), others['cumulative_uniques_%'].to_list()[-1]]
    top_features = top_features + ['others']
  # details
  filtered_percent = round((top_features_n / features_n) * 100, 2)
  print(f'\nMinimum coverage: {minimum_coverage}%\nFiltered "{by}": {top_features_n}/{features_n} ({filtered_percent}%)\nSelected: {top_features}\n')
  # fig 1
  if top_features_n > 0: top_string = f' (top {top_features_n} and others)'
  else: top_string = ''
  # filters dataframe with each feature to aggregate stats into top_features_df
  for feature in top_features:
    if feature == 'others':
        filter_df = others
    else:
      filter_df = dataframe.copy()
      filter_df['/filter'] = dataframe[by].str.contains(feature)
      filter_df = filter_df[filter_df['/filter'] == True].drop('/filter', axis=1)
    top_features_df.loc[feature, 'size'] = filter_df.shape[0] * filter_df.shape[1]
    top_features_df.loc[feature, 'nans'] = filter_df.isna().sum().sum()
    top_features_df.loc[feature, 'unique'] = filter_df.nunique().sum().sum()

  top_features_df['fill'] = top_features_df['size'] - top_features_df['nans']
  top_features_df['nans_%'] = ((top_features_df['nans'] / top_features_df['size']) * 100).round(2)
  top_features_df['fill_%'] = 100 - top_features_df['nans_%']
  top_features_df['uniques_%'] = ((top_features_df['unique'] / top_features_df['size']) * 100).round(2)
  top_features_df = top_features_df[['population', 'population_%', 'cumulative_uniques_%', 'fill', 'fill_%', 'nans', 'nans_%', 'unique', 'uniques_%', 'size']]
  top_features_fig = top_features_df[['population_%', 'fill_%', 'nans_%', 'uniques_%']].transpose()
  top_features_fig = go.Figure(data=[go.Bar(name=str(top_features_fig.index[index]), x=list(top_features_fig.columns.values), y=list(top_features_fig.iloc[index,:].values)) for index in range(top_features_fig.shape[0])])
  top_features_fig.update_layout(template=template,title=f'"{by}" charateristics per category' + top_string) #width=1200, height=600, 
  top_features_fig.show()

  return top_features_df


### *c -* PCA

These are functions from the *OpenClassRooms* course on *Dimensionality Reduction*.

*You can skip this part in you are not interested in code.*

In [ ]:
def display_circles(pcs, n_comp, pca, axis_ranks, labels=None, label_rotation=0, lims=None):
    for d1, d2 in axis_ranks: # On affiche les 3 premiers plans factoriels, donc les 6 premières composantes
        if d2 < n_comp:

            # initialisation de la figure
            fig, ax = plt.subplots(figsize=(14,12))

            # détermination des limites du graphique
            if lims is not None :
                xmin, xmax, ymin, ymax = lims
            elif pcs.shape[1] < 30 :
                xmin, xmax, ymin, ymax = -1, 1, -1, 1
            else :
                xmin, xmax, ymin, ymax = min(pcs[d1,:]), max(pcs[d1,:]), min(pcs[d2,:]), max(pcs[d2,:])

            # affichage des flèches
            # s'il y a plus de 30 flèches, on n'affiche pas le triangle à leur extrémité
            if pcs.shape[1] < 30 :
                plt.quiver(np.zeros(pcs.shape[1]), np.zeros(pcs.shape[1]),
                   pcs[d1,:], pcs[d2,:], 
                   angles='xy', scale_units='xy', scale=1, color="grey")
                # (voir la doc : https://matplotlib.org/api/_as_gen/matplotlib.pyplot.quiver.html)
            else:
                lines = [[[0,0],[x,y]] for x,y in pcs[[d1,d2]].T]
                ax.add_collection(LineCollection(lines, axes=ax, alpha=.1, color='black'))
            
            # affichage des noms des variables  
            if labels is not None:  
                for i,(x, y) in enumerate(pcs[[d1,d2]].T):
                    if x >= xmin and x <= xmax and y >= ymin and y <= ymax :
                        plt.text(x, y, labels[i], fontsize='14', ha='center', va='center', rotation=label_rotation, color="blue", alpha=0.5)
            
            # affichage du cercle
            circle = plt.Circle((0,0), 1, facecolor='none', edgecolor='b')
            plt.gca().add_artist(circle)

            # définition des limites du graphique
            plt.xlim(xmin, xmax)
            plt.ylim(ymin, ymax)
        
            # affichage des lignes horizontales et verticales
            plt.plot([-1, 1], [0, 0], color='grey', ls='--')
            plt.plot([0, 0], [-1, 1], color='grey', ls='--')

            # nom des axes, avec le pourcentage d'inertie expliqué
            plt.xlabel('F{} ({}%)'.format(d1+1, round(100*pca.explained_variance_ratio_[d1],1)))
            plt.ylabel('F{} ({}%)'.format(d2+1, round(100*pca.explained_variance_ratio_[d2],1)))

            plt.title("Cercle des corrélations (F{} et F{})".format(d1+1, d2+1))
            plt.show(block=False)
        

def display_factorial_planes(X_projected, n_comp, pca, axis_ranks, labels=None, alpha=1, illustrative_var=None):
    for d1,d2 in axis_ranks:
        if d2 < n_comp:
 
            # initialisation de la figure       
            fig = plt.figure(figsize=(14,12))
        
            # affichage des points
            if illustrative_var is None:
                plt.scatter(X_projected[:, d1], X_projected[:, d2], alpha=alpha)
            else:
                illustrative_var = np.array(illustrative_var)
                for value in np.unique(illustrative_var):
                    selected = np.where(illustrative_var == value)
                    plt.scatter(X_projected[selected, d1], X_projected[selected, d2], alpha=alpha, label=value)
                plt.legend()

            # affichage des labels des points
            if labels is not None:
                for i,(x,y) in enumerate(X_projected[:,[d1,d2]]):
                    plt.text(x, y, labels[i],
                              fontsize='14', ha='center',va='center') 
                
            # détermination des limites du graphique
            boundary = np.max(np.abs(X_projected[:, [d1,d2]])) * 1.1
            plt.xlim([-boundary,boundary])
            plt.ylim([-boundary,boundary])
        
            # affichage des lignes horizontales et verticales
            plt.plot([-100, 100], [0, 0], color='grey', ls='--')
            plt.plot([0, 0], [-100, 100], color='grey', ls='--')

            # nom des axes, avec le pourcentage d'inertie expliqué
            plt.xlabel('F{} ({}%)'.format(d1+1, round(100*pca.explained_variance_ratio_[d1],1)))
            plt.ylabel('F{} ({}%)'.format(d2+1, round(100*pca.explained_variance_ratio_[d2],1)))

            plt.title("Projection des individus (sur F{} et F{})".format(d1+1, d2+1))
            plt.show(block=False)


def display_scree_plot(pca):
    scree = pca.explained_variance_ratio_*100
    plt.figure(figsize=(14,12))
    plt.bar(np.arange(len(scree))+1, scree)
    plt.plot(np.arange(len(scree))+1, scree.cumsum(),c="red",marker='o')
    plt.xlabel("rang de l'axe d'inertie")
    plt.ylabel("pourcentage d'inertie")
    plt.title("Eboulis des valeurs propres")


def dimensional_reduction(dataframe:pd.DataFrame,third_dimension:str,n_comp=4):

  X = get_num(dataframe)
  X_features = dataframe.columns

  n, p = X.shape[0], X.shape[1]
  n_comp = 4

  standard_scaler = StandardScaler()
  X_scaled = standard_scaler.fit_transform(X)

  pca = PCA(svd_solver='full', n_components=n_comp)
  X_projected = pca.fit_transform(X_scaled)

  display_scree_plot(pca)
  display_circles(pca.components_, n_comp, pca, [(0,1),(2,3),(4,5)], labels = X_features)
  display_factorial_planes(X_projected, n_comp, pca, [(0,1),(2,3),(4,5)], illustrative_var=dataframe[third_dimension].values)

## *C -* Mouting Google Drive

In order to load the data which has been downloaded from *Kaggle* and uploaded to my personnal drive, we need to mount the Google Drive instance.

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive') # link to be updated

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


## *D -* Loading the Data

In [ ]:
root_path = './gdrive/MyDrive/OpenClassrooms/P3'
dataframe_2015 = pd.read_csv(f'{root_path}/2015-building-energy-benchmarking.csv', sep=',', encoding="utf-8", low_memory=True, index_col=0)
dataframe_2016 = pd.read_csv(f'{root_path}/2016-building-energy-benchmarking.csv', sep=',', encoding="utf-8", low_memory=True, index_col=0)

# ***1 -*** **Cleaning and Exploration**

## *A -* Dictionnary

1. We load the meta data *.json* file available at the Kaggle repository:

In [ ]:
with open(f'{root_path}/socrata_metadata_2016-building-energy-benchmarking.json') as json_data:
    dict_data = json.load(json_data)

2. We create a Dataframe from the dictionnary structured object:

In [ ]:
features_df = pd.DataFrame.from_dict(dict_data['columns']).set_index('id')
features_df.head()

name  ...  width
id                              ...       
349768636        OSEBuildingID  ...    NaN
349768619             DataYear  ...  100.0
349768631         BuildingType  ...    NaN
349768622  PrimaryPropertyType  ...    NaN
349768617         PropertyName  ...    NaN

[5 rows x 10 columns]

3. Using the generated dataframe, we print each feature and its description:

In [ ]:
for name, col_type, description in zip(features_df['name'].values, features_df['dataTypeName'], features_df['description'].values):
  print(f"{name} ({col_type}): {description}\n")

OSEBuildingID (number): A unique identifier assigned to each property covered by the Seattle Benchmarking Ordinance for tracking and identification purposes.

DataYear (number): Calendar year (January-December) represented by each data record.

BuildingType (text): City of Seattle building type classification.

PrimaryPropertyType (text): The primary use of a property (e.g. office, retail store). Primary use is defined as a function that accounts for more than 50% of a property. This is the Property Type - EPA Calculated field from Portfolio Manager.

PropertyName (text): Official or common property name as entered in EPA’s Portfolio Manager.

Address (text): Property street address

City (text): Property city

State (text): Property state

ZipCode (number): Property zip

TaxParcelIdentificationNumber (text): Property King County PIN 

CouncilDistrictCode (number): Property City of Seattle council district.

Neighborhood (text): Property neighborhood area defined by the City of Seattle

## *B -* Data Join

For this project, we dispose of two separate datasets:
* According to the *data dictionnary*, the 2016 datasets metrics coincides with the 2015s metrics.
* This can be verified by checking out the 2015s *data dictionnary*.
* There are also several columns that aren't present in the 2016 dataset. 
* We will take the 2016 as a reference and format the 2015 dataset accordingly.
* Let's take a look at the difference in terms of index:

In [ ]:
ids_diff = dataframe_2015.index.difference(dataframe_2016.index) # We remove the ids already present in the 2016 dataset
print(f'Number of samples not present in the 2016 dataset: {len(ids_diff)}')

Number of samples not present in the 2016 dataset: 56


1. We select the buildings that are not present in the 2016 dataset thanks to the *OSEBuildingID*:

In [ ]:
dataframe_2015 = dataframe_2015.loc[ids_diff,:]
dataframe_2015.shape

(56, 46)

* What about columns ?

In [ ]:
set(dataframe_2015.columns).difference(set(dataframe_2016.columns))

{'2010 Census Tracts',
 'City Council Districts',
 'Comment',
 'GHGEmissions(MetricTonsCO2e)',
 'GHGEmissionsIntensity(kgCO2e/ft2)',
 'Location',
 'OtherFuelUse(kBtu)',
 'SPD Beats',
 'Seattle Police Department Micro Community Policing Plan Areas',
 'Zip Codes'}

2. We rename the common columns to the 2016 names:

In [ ]:
dataframe_2015 = dataframe_2015.rename({'GHGEmissions(MetricTonsCO2e)':'TotalGHGEmissions',
 'GHGEmissionsIntensity(kgCO2e/ft2)':'GHGEmissionsIntensity', 'Comment': 'Comments'}, axis=1)
dataframe_2015.head()

DataYear          BuildingType  ... SPD Beats Zip Codes
OSEBuildingID                                  ...                    
61                 2015  Multifamily LR (1-4)  ...      30.0     18081
266                2015  Multifamily LR (1-4)  ...      51.0     19581
325                2015        NonResidential  ...      31.0     18081
400                2015        NonResidential  ...      30.0     18081
442                2015        NonResidential  ...       7.0     18390

[5 rows x 46 columns]

* Let's take a look at the location column of the 2015 dataset:

In [ ]:
sample(dataframe_2015['Location'])

Location  Location_index
sample                                                                   
0       {'latitude': '47.613922', 'longitude': '-122.3...              50
1       {'latitude': '47.70384555', 'longitude': '-122...              34
2       {'latitude': '47.72028152', 'longitude': '-122...              49
3       {'latitude': '47.57089656', 'longitude': '-122...               5
4       {'latitude': '47.64360097', 'longitude': '-122...              19
5       {'latitude': '47.58809497', 'longitude': '-122...              39
6       {'latitude': '47.6590538024902', 'longitude': ...              54
7       {'latitude': '47.73219752', 'longitude': '-122...              41
8       {'latitude': '47.62811223', 'longitude': '-122...              55
9       {'latitude': '47.61522339', 'longitude': '-122...              32

3. We "unzip" the *Location* column, which is a dictionnary containing all the location data into the columns corresponding to the 2016 dataset:

In [ ]:
def unzip_location(cell):
  cell_dict = eval(cell)
  latitude, longitude = cell_dict['latitude'], cell_dict['longitude']
  address_dict = eval(cell_dict['human_address'])
  address, city, state, zip = address_dict['address'], address_dict['city'], address_dict['state'], address_dict['zip']
  return latitude, longitude, address, city, state, zip

dataframe_2015['Latitude'], dataframe_2015['Longitude'], dataframe_2015['Address'], dataframe_2015['City'], dataframe_2015['State'], dataframe_2015['ZipCode'] = zip(*dataframe_2015['Location'].apply(unzip_location))
dataframe_2015.head()

DataYear          BuildingType  ... State ZipCode
OSEBuildingID                                  ...              
61                 2015  Multifamily LR (1-4)  ...    WA   98101
266                2015  Multifamily LR (1-4)  ...    WA   98126
325                2015        NonResidential  ...    WA   98101
400                2015        NonResidential  ...    WA   98101
442                2015        NonResidential  ...    WA   98109

[5 rows x 52 columns]

4. We select the columns of the 2015 dataset in accordance to the 2016 dataset:

In [ ]:
dataframe_2015 = dataframe_2015[dataframe_2016.columns]
dataframe_2015.head()

DataYear  ... GHGEmissionsIntensity
OSEBuildingID            ...                      
61                 2015  ...                  2.19
266                2015  ...                  0.06
325                2015  ...                  0.24
400                2015  ...                  0.20
442                2015  ...                  0.23

[5 rows x 45 columns]

5. We concat the 2 dataframes and check that we don't have duplicates:

In [ ]:
dataframe = pd.concat([dataframe_2015, dataframe_2016])
pd.DataFrame(dataframe.index.value_counts()).head()

OSEBuildingID
24688              1
677                1
673                1
27296              1
25245              1

* Everything looks in order.

## *C -* Filtering

As mentionned in the introduction of this project, we are working with the non residential buildings of the dataset.

Therefore, we need to filter the dataset in order to keep the non residential buildings only.

1. We dispose of the "LargestPropertyUseType" feature.

In [ ]:
sample(dataframe['BuildingType'])

BuildingType  BuildingType_index
sample                                          
0       Multifamily LR (1-4)               27361
1       Multifamily HR (10+)               20772
2       Multifamily MR (5-9)               49901
3             NonResidential               27874
4       Multifamily LR (1-4)               24068
5             NonResidential               21496
6         Nonresidential COS                 358
7             NonResidential               49985
8             NonResidential               27903
9       Multifamily MR (5-9)               50027

2. We can use it to filter the dataset by building use:

In [ ]:
filter_cat_feature(dataframe, 'BuildingType', 100)


Minimum coverage: 100%
Filtered "BuildingType": 0/8 (0.0%)
Selected: ['NonResidential', 'Multifamily LR (1-4)', 'Multifamily MR (5-9)', 'Multifamily HR (10+)', 'SPS-District K-12', 'Nonresidential COS', 'Campus', 'Nonresidential WA']



/usr/local/lib/python3.7/dist-packages/pandas/core/strings.py:2001: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/usr/local/lib/python3.7/dist-packages/pandas/core/strings.py:2001: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/usr/local/lib/python3.7/dist-packages/pandas/core/strings.py:2001: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.



population  population_%  ...  uniques_%     size
tag                                             ...                    
NonResidential              1488         43.36  ...      41.26  66960.0
Multifamily LR (1-4)        1040         30.30  ...        NaN      0.0
Multifamily MR (5-9)         584         17.02  ...        NaN      0.0
Multifamily HR (10+)         110          3.21  ...        NaN      0.0
SPS-District K-12             99          2.88  ...      43.61   4455.0
Nonresidential COS            85          2.48  ...      50.33   3825.0
Campus                        25          0.73  ...      57.60   1125.0
Nonresidential WA              1          0.03  ...      82.22     45.0

[8 rows x 10 columns]

3. We select the the types of building which aren't housing (not *Multifamily*):

In [ ]:
shape = dataframe.shape
dataframe = dataframe[~dataframe['BuildingType'].str.startswith('Multifamily')] # We select the features thatdon't start with "Multifamily"
dataframe_columns = dataframe.columns
shape_diff(shape,dataframe.shape)
dataset = Dataset(dataframe)

Dropped samples: 1734
Version 0: "original" initialized


4. We are now ready for the cleaning and data exploration.

## *D -* Head 

Let's take a look at the head (the firsts rows) of the dataset:

In [ ]:
dataframe.head()

DataYear  ... GHGEmissionsIntensity
OSEBuildingID            ...                      
325                2015  ...                  0.24
400                2015  ...                  0.20
442                2015  ...                  0.23
499                2015  ...                  1.63
559                2015  ...                  0.99

[5 rows x 45 columns]

* Everything looks in order.

## *E -* Shape

In [ ]:
samples, features = dataset.get('samples'), dataset.get('features')
print(f'The dataset is composed of {samples} samples (rows), and {features} features (columns).')

The dataset is composed of 1698 samples (rows), and 45 features (columns).


## *F -* Dtypes

In [ ]:
dtypes = sum_dtypes(dataframe)

* About a third of the dataset features are categorical while the rest are numerical.

## *G -* NaNs

* The are some NaNs in the dataset.

In [ ]:
nans = sum_nans(dataframe)
nans.head()

nans  nans_%
feature                                     
Comments                        1697   99.94
Outlier                         1679   98.88
YearsENERGYSTARCertified        1599   94.17
ThirdLargestPropertyUseType     1342   79.03
ThirdLargestPropertyUseTypeGFA  1342   79.03

In [ ]:
average_nans = round(nans['nans_%'].mean(), 2)
print(f'The dataset is empty at {average_nans} %')

The dataset is empty at 13.09 %


## *H -* Uniques

In [ ]:
uniques = sum_uniques(dataframe)
uniques.head()

uniques  uniques_%
feature                                
PropertyName            1694      99.76
Electricity(kBtu)       1684      99.18
Electricity(kWh)        1684      99.18
SiteEnergyUse(kBtu)     1680      98.94
Address                 1677      98.76

In [ ]:
average_uniques = round(uniques['uniques_%'].mean(), 2)
print(f'The dataset contains {average_uniques} % of unique values') 

The dataset contains 40.64 % of unique values


## *I -* Numericals

Now, let's take a look at the numerical features report:

In [ ]:
dataset.num_report(fig_fill_min=75)

* Some features are predominently filled with zeroes, such as *SteamUse(kBtu)* or *PropertyGFAParking*, which should not alert us, as not every building uses steam or has a parking.



In [ ]:
dataset.get('numericals')

count  fill_%  ...           75%           max
feature                                          ...                            
DataYear                         1698.0  100.00  ...  2.016000e+03  2.016000e+03
YearBuilt                        1698.0  100.00  ...  1.989000e+03  2.015000e+03
NumberofFloors                   1698.0  100.00  ...  4.000000e+00  9.900000e+01
PropertyGFATotal                 1698.0  100.00  ...  1.050902e+05  9.320156e+06
PropertyGFAParking               1698.0  100.00  ...  0.000000e+00  5.126080e+05
PropertyGFABuilding(s)           1698.0  100.00  ...  9.465975e+04  9.320156e+06
CouncilDistrictCode              1698.0  100.00  ...  7.000000e+00  7.000000e+00
NumberofBuildings                1696.0   99.88  ...  1.000000e+00  1.110000e+02
SiteEnergyUse(kBtu)              1695.0   99.82  ...  6.867819e+06  8.739237e+08
TotalGHGEmissions                1695.0   99.82  ...  1.421550e+02  1.687098e+04
NaturalGas(kBtu)                 1695.0   99.82  ...  1.522622e+06  2.979090e+08
NaturalGas(therms)               1695.0   99.82  ...  1.522621e+04  2.979090e+06
Electricity(kBtu)                1695.0   99.82  ...  4.821154e+06  6.570744e+08
Electricity(kWh)                 1695.0   99.82  ...  1.412999e+06  1.925775e+08
SteamUse(kBtu)                   1695.0   99.82  ...  0.000000e+00  1.349435e+08
GHGEmissionsIntensity            1695.0   99.82  ...  1.890000e+00  3.409000e+01
SourceEUIWN(kBtu/sf)             1695.0   99.82  ...  2.056000e+02  2.620000e+03
SourceEUI(kBtu/sf)               1695.0   99.82  ...  2.039000e+02  2.620000e+03
SiteEnergyUseWN(kBtu)            1694.0   99.76  ...  7.100034e+06  4.716139e+08
SiteEUIWN(kBtu/sf)               1694.0   99.76  ...  8.520000e+01  8.344000e+02
SiteEUI(kBtu/sf)                 1694.0   99.76  ...  8.170000e+01  8.344000e+02
LargestPropertyUseTypeGFA        1686.0   99.29  ...  9.200450e+04  9.320156e+06
ENERGYSTARScore                  1112.0   65.49  ...  8.900000e+01  1.000000e+02
SecondLargestPropertyUseTypeGFA   866.0   51.00  ...  3.197325e+04  6.867500e+05
ThirdLargestPropertyUseTypeGFA    356.0   20.97  ...  1.253525e+04  4.597480e+05

[25 rows x 13 columns]

* We notice that there are outliers in the dataset, such as negative values in *TotalGHGEmissions* or *Electricity(kBtu)*. 
* We handle these outliers to ensure our data is qualitative enough for training machine learning models:

In [ ]:
shape = dataframe.shape
dataframe.loc[dataframe['TotalGHGEmissions'] < 0, 'DetectedOutlier'] = 1 # We create a feature to detect the outliers
dataframe.loc[dataframe['Electricity(kBtu)'] < 0, 'DetectedOutlier'] = 1
dataframe['DetectedOutlier'] = dataframe['DetectedOutlier'].fillna(0)
dataframe = dataframe[dataframe['DetectedOutlier'] == 0] # We filter the dataset using the created filter feature
dataframe = dataframe.drop('DetectedOutlier', axis = 1) # We drop the filter feature
shape_diff(shape,dataframe.shape)

Dropped samples: 1


## *J -* Categoricals

What about the categorical features ?

In [ ]:
dataset.cat_report(fig_fill_min=75)

* Some features, such as *BuildingType*, *PrimaryPropertyType* or *Neighborhood* have a small ratio of unique values, which means they will be of interest to filter the dataset.

In [ ]:
dataset.get('categoricals')

count  ...  freq
feature                              ...      
BuildingType                   1698  ...  1488
TaxParcelIdentificationNumber  1698  ...     8
ComplianceStatus               1698  ...  1578
DefaultData                    1698  ...  1580
PrimaryPropertyType            1698  ...   299
Latitude                       1698  ...     9
Neighborhood                   1698  ...   370
Longitude                      1698  ...     8
State                          1698  ...  1698
City                           1698  ...  1668
Address                        1698  ...     4
PropertyName                   1698  ...     2
ListOfAllPropertyUseTypes      1690  ...   144
LargestPropertyUseType         1686  ...   507
ZipCode                        1682  ...   182
SecondLargestPropertyUseType    866  ...   343
ThirdLargestPropertyUseType     356  ...    49
YearsENERGYSTARCertified         99  ...    12
Outlier                          19  ...    15
Comments                          1  ...     1

[20 rows x 8 columns]

# ***2 -*** **Going Deeper**

## *A -* Targets

Our mission is to predict the energy use and greenhouse gas emissions of the buildings, to do so, we will select as targets:
* *SiteEnergyUseWN(kBtu)*
* *TotalGHGEmissions*

We choose to use the *Weather Normalized* feature as a target as it normalizes the data with a 30 years average. 
* This will foolproof our models against extreme and ponctual weather conditions.

We can plot the two targets:

In [ ]:
plot_series_vs(dataframe['SiteEnergyUseWN(kBtu)'], dataframe['TotalGHGEmissions'], dataframe['PropertyGFATotal'])

In [ ]:
plot_series_vs(dataframe['SiteEnergyUseWN(kBtu)'], dataframe['TotalGHGEmissions'], dataframe['PrimaryPropertyType'], 'category')

* By the looks of these graphs, we can alredy infer that the 2 targets are highly correlated.

## *B -* Meta data

Some meta data features do not give us valuable information:
* *DataYear*, we are using the 2016 data,
* *Comments* is filled with zeroes at 100%,

We remove them:

In [ ]:
shape = dataframe.shape
dataframe = dataframe.drop([
  'Comments',
  'DataYear'], axis=1) # We drop the unwanted features
shape_diff(shape,dataframe.shape)

Dropped features: 2


Other features can be use to select the most qualitative samples:

### *a -* DefaultData

In [ ]:
pd.DataFrame(dataframe['DefaultData'].value_counts())

DefaultData
False         1579
True            88
No              25
Yes              5

* We select the samples that aren't default data and drop the filter feature:

In [ ]:
dataframe[dataframe['DefaultData'] == False]
dataframe = dataframe.drop('DefaultData', axis=1)

### *b -* ComplianceStatus

In [ ]:
pd.DataFrame(dataframe['ComplianceStatus'].value_counts())

ComplianceStatus
Compliant                                 1577
Error - Correct Default Data                88
Non-Compliant                               18
Missing Data                                14

* We select the compliant data and drop the filter feature:

In [ ]:
dataframe[dataframe['ComplianceStatus'] == 'Compliant']
dataframe = dataframe.drop('ComplianceStatus', axis=1)

### *c -* Outlier

In [ ]:
pd.DataFrame(dataframe['Outlier'].value_counts())

Outlier
Low outlier        15
High outlier        2
Low Outlier         2

* We select the samples that aren't outliers and drop the filter feature:

In [ ]:
dataframe[dataframe['Outlier'] == 0]
dataframe = dataframe.drop('Outlier', axis=1)

## *C -* Administrative data


* Other features are of low interest to us, as they don't convey data about our targets, such as the *TaxParcelIdentificationNumber*, *PropertyName* or *CouncilDistrictCode*, we remove them:


In [ ]:
shape = dataframe.shape
dataframe = dataframe.drop([
  'TaxParcelIdentificationNumber',
  'CouncilDistrictCode',
  'PropertyName'
  ], axis=1)
shape_diff(shape,dataframe.shape)

Dropped features: 3


## *D -* Location data

We have plenty of location features, we have to select the most useable features:
* *City* and *State* features are filled with an unique value,  which doesn't give us information as we already know that we are working with Seattles data. We won't use these features.
* *Adress*, *PropertyName* and *ZipCode* features would require a lot of processing to be useable.

We drop them:

In [ ]:
shape = dataframe.shape
dataframe = dataframe.drop([
  'City',
  'State',
  'Address',
  'ZipCode'
  ], axis=1)
shape_diff(shape,dataframe.shape)
dataset.save_version(dataframe, 'features_preselection')

Dropped features: 4

Version 1: "features_preselection" saved



###  *a -* Neighborhood

In [ ]:
sample(dataframe['Neighborhood'])

Neighborhood  Neighborhood_index
sample                                            
0                    SOUTHWEST                  12
1                    NORTHEAST                   8
2                    NORTHWEST                   4
3       DELRIDGE NEIGHBORHOODS                  18
4                    SOUTHEAST                   5
5                      CENTRAL                  11
6                      Central                   9
7                     DELRIDGE                  13
8                   LAKE UNION                   1
9                        NORTH                  10

* *Neighborhood* modalities aren't standarized: some are capitalized, other are in caps. For example, there are two modalities for Delrigde: *Delridge* and *DELRIDGE NEIGHBORHOODS*
* We clean the feature:

In [ ]:
to_drop_neighborhood = ['lake','greater','neighborhoods', '/', 'queen', 'anne'] # We drop the extra characters

dataframe['CleanedNeighborhood'] = dataframe['Neighborhood'].str.lower()

for string in to_drop_neighborhood:
  dataframe['CleanedNeighborhood'] = dataframe['CleanedNeighborhood'].str.replace(string,'')
  
dataframe['CleanedNeighborhood'] = dataframe['CleanedNeighborhood'].str.strip()
dataframe = dataframe.drop('Neighborhood',axis=1)

In [ ]:
pie_plot(dataframe, 'CleanedNeighborhood')

* We can know take a look into the cleaned modalities:

In [ ]:
filter_cat_feature(dataframe, 'CleanedNeighborhood', 90)


Minimum coverage: 90%
Filtered "CleanedNeighborhood": 10/13 (76.92%)
Selected: ['downtown', 'duwamish', 'magnolia', 'union', 'northeast', 'east', 'northwest', 'ballard', 'north', 'central', 'others']



population  population_%  ...  uniques_%     size
tag                                  ...                    
downtown        370.0         21.80  ...      54.21  12210.0
duwamish        349.0         20.57  ...      51.14  11517.0
magnolia        155.0          9.13  ...      55.09   5115.0
union           151.0          8.90  ...      58.70   4983.0
northeast       128.0          7.54  ...      55.66   4224.0
east            125.0          7.37  ...      54.16   9933.0
northwest        89.0          5.24  ...      57.61   2937.0
ballard          72.0          4.24  ...      60.02   2376.0
north            67.0          3.95  ...      52.69   9372.0
central          55.0          3.24  ...      59.23   1815.0
others          136.0          8.02  ...     100.00      9.0

[11 rows x 10 columns]

* We use the *anova* wrapper function to calculate the Eta² scores, which beforehand normalizes the distributions:

In [ ]:
anova(dataframe, 'CleanedNeighborhood')

* *Neighborhood* has a moderate impact on *Yearbuilt*, *NumberofFloors* and *PropertyGFATotal*, and of course: a high impact on *Latitude* and *Longitude*.

In [ ]:
batch_box_plots(dataframe, 'CleanedNeighborhood')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:240: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:243: RuntimeWarning:

invalid value encountered in double_scalars



In [ ]:
dataframe_2015.head(50)

DataYear  ... GHGEmissionsIntensity
OSEBuildingID            ...                      
61                 2015  ...                  2.19
266                2015  ...                  0.06
325                2015  ...                  0.24
400                2015  ...                  0.20
442                2015  ...                  0.23
499                2015  ...                  1.63
559                2015  ...                  0.99
560                2015  ...                  0.06
675                2015  ...                  4.02
714                2015  ...                  1.27
790                2015  ...                  0.70
838                2015  ...                  2.64
19656              2015  ...                  0.02
19658              2015  ...                  0.35
19780              2015  ...                 10.29
19882              2015  ...                  1.07
19905              2015  ...                  1.11
19947              2015  ...                  0.06
20152              2015  ...                  0.08
20658              2015  ...                  0.07
21237              2015  ...                  1.33
21471              2015  ...                  0.06
21555              2015  ...                  0.07
21688              2015  ...                  1.24
21796              2015  ...                  0.70
22138              2015  ...                  0.01
22172              2015  ...                  0.05
22441              2015  ...                  1.00
22446              2015  ...                  0.11
22808              2015  ...                  0.07
23163              2015  ...                  0.11
23308              2015  ...                  0.07
23848              2015  ...                  2.76
24068              2015  ...                  0.07
24168              2015  ...                  0.06
24194              2015  ...                  0.02
24408              2015  ...                   NaN
24739              2015  ...                  2.60
24904              2015  ...                  0.66
25042              2015  ...                  0.65
25455              2015  ...                  5.59
25617              2015  ...                  0.08
25654              2015  ...                  0.02
25701              2015  ...                  0.06
25821              2015  ...                  1.51
26938              2015  ...                  0.08
27355              2015  ...                  0.07
27639              2015  ...                  3.85
27699              2015  ...                  0.06
27706              2015  ...                  0.07

[50 rows x 45 columns]

### *b -* Latitude & Longitude

* Localisation features that we can easily use are *Latitude* and *Longitude*.
* The distance from the city center could make for a valuable machine learning feature.
We can plot the building locations:

In [ ]:
sea_coords = (47.61,-122.33)

seattle_map = folium.Map(location=sea_coords, zoom_start=10)

marker_cluster = folium.plugins.MarkerCluster().add_to(seattle_map)
for latitude, longitude, in zip(dataframe['Latitude'].astype(float), dataframe['Longitude'].astype(float)):
    folium.Marker(location=[latitude, longitude]).add_to(marker_cluster)

seattle_map

## *E -* Structural data

### *a -* YearBuilt

* Using the *YearBuilt* feature, we create a *CalculatedBuildingAge* feature with the year 2016 (the year the data has been collected) as a reference:

In [ ]:
year = 2016
dataframe['CalculatedBuildingAge'] = year - dataframe['YearBuilt']
dataframe = dataframe.drop('YearBuilt', axis = 1)

* We can now plot the ages of the buildings:

In [ ]:
bar_plot(dataframe,'CalculatedBuildingAge')

* Building ages are uniform with an important amount of noise, with and exception: there few buildings that are 70 to 85 years old.

### *b -* BuildingType

In [ ]:
pie_plot(dataframe, 'BuildingType')

In [ ]:
filter_cat_feature(dataframe, 'BuildingType')


Minimum coverage: 100%
Filtered "BuildingType": 0/5 (0.0%)
Selected: ['NonResidential', 'SPS-District K-12', 'Nonresidential COS', 'Campus', 'Nonresidential WA']



population  population_%  ...  uniques_%     size
tag                                           ...                    
NonResidential            1487         87.63  ...      47.16  49071.0
SPS-District K-12           99          5.83  ...      48.91   3267.0
Nonresidential COS          85          5.01  ...      58.86   2805.0
Campus                      25          1.47  ...      65.94    825.0
Nonresidential WA            1          0.06  ...      81.82     33.0

[5 rows x 10 columns]

* The *NonResidential* modality represents more than 80% of the entire population

In [ ]:
anova(dataframe,'BuildingType')

* The Anova shows that the *BuildingType* has a moderate impact on the numerical features.

In [ ]:
batch_box_plots(dataframe, 'BuildingType')

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:240: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:243: RuntimeWarning:

invalid value encountered in double_scalars



* The *Campus* type presents extreme values while it represents only 1,44% of the population.
* We have to contemplate the idea that the *Campus* samples should be considered as outliers.

### *c -* Floors and Buildings

In [ ]:
bar_plot(dataframe,'NumberofFloors')

In [ ]:
bar_plot(dataframe,'NumberofBuildings')

* Some rows contain null values which we can consider as missing data, as every building should have a minimum of 1 building and 1 floor. We will have to handle this missing data in our feature engineering.

## *F -* Energy Data

### *a -* Correlations

We assume that some of the features are highly correlated, as they represent the same data in different formats.
* Let's take a look at the correlations matrix:

In [ ]:
energy_features = get_feat(dataframe,')',inverse=True) + ['TotalGHGEmissions','GHGEmissionsIntensity']
energy_features.remove('PropertyGFABuilding(s)')
heatmap(dataframe[energy_features].corr().round(2))

* We notice that some groups of features are highly correlated, thus redundant.

### *b -* Redundants

Energy inputs and outputs features are sometimes redundant, we will need to pick non-redundant features to train our model:
* We choose to use kBtu features, as they enable to compare electricity, steam, natural gas and even energy with the same standard.
* We arbritrarily remove the features by *square feet*.
* We remove the weather normalized features.

In [ ]:
redundants = [
  'SiteEUIWN(kBtu/sf)',
  'SiteEUI(kBtu/sf)',
  'SiteEnergyUse(kBtu)',
  'SourceEUI(kBtu/sf)',
  'Electricity(kWh)',
  'NaturalGas(therms)',
  'GHGEmissionsIntensity'
  ]
dataframe = dataframe.drop(redundants, axis=1)

## *G -* Uses data

In [ ]:
pie_plot(dataframe, 'PrimaryPropertyType')

* *Small and Mid-Sized Offices*, *Warehouse*, *Large Offices* and *K-12 schools* constitude close to a half of the entire population.

In [ ]:
filter_cat_feature(dataframe, 'PrimaryPropertyType', 90)


Minimum coverage: 90%
Filtered "PrimaryPropertyType": 12/24 (50.0%)
Selected: ['Small- and Mid-Sized Office', 'Other', 'Warehouse', 'Large Office', 'K-12 School', 'Mixed Use Property', 'Retail Store', 'Hotel', 'Worship Facility', 'Distribution Center', 'Medical Office', 'Supermarket / Grocery Store', 'others']



population  population_%  ...  uniques_%    size
tag                                                    ...                   
Small- and Mid-Sized Office       298.0         17.56  ...      43.07  7748.0
Other                             257.0         15.14  ...      44.75  6682.0
Warehouse                         187.0         11.02  ...      42.69  5226.0
Large Office                      176.0         10.37  ...      51.97  4576.0
K-12 School                       141.0          8.31  ...      40.53  3666.0
Mixed Use Property                115.0          6.78  ...      54.82  2990.0
Retail Store                       94.0          5.54  ...      45.34  2444.0
Hotel                              76.0          4.48  ...      51.16  1976.0
Worship Facility                   72.0          4.24  ...      46.05  1872.0
Distribution Center                53.0          3.12  ...      48.19  1378.0
Medical Office                     42.0          2.47  ...      52.66  1092.0
Supermarket / Grocery Store        40.0          2.36  ...      48.75  1040.0
others                            146.0          8.62  ...      83.33    36.0

[13 rows x 10 columns]

In [ ]:
anova(dataframe, 'PrimaryPropertyType')

* The Anova shows that *PrimaryPropertyType* has an impact on several numerical features.
* The property types might therefore be very important features for our models.

## *Excluded*

We will exclude some features of the analysis in order to improve our graphs readability:

In [ ]:
excluded = [
  'Latitude',
  'Longitude',
  'ListOfAllPropertyUseTypes',
  'LargestPropertyUseType',
  'LargestPropertyUseTypeGFA',
  'SecondLargestPropertyUseType',
  'SecondLargestPropertyUseTypeGFA',
  'ThirdLargestPropertyUseType',
  'ThirdLargestPropertyUseTypeGFA'
  ]

## *H -* Correlations

In [ ]:
heatmap(dataframe.drop(excluded,axis=1).select_dtypes([int,float]).corr().round(2))

* We confirm that the targets *SiteEnergyUseWN(kBtu)* and *TotalGHGEmissions* are highly correlated with a Pearson correlation as high as 0.86.
* Several other features are highly correlated, during the feature engineering we will try to reduce their number, as this could be detrimental to our modelling, especially for the linear algorythms.

In [ ]:
dual_scatter_matrix(dataframe.drop(excluded,axis=1),'CalculatedBuildingAge',split_corr=0.6)

## *I -* Distributions

* We plot the distributions of our numerical features:

In [ ]:
plot_distributions(dataframe.drop(excluded,axis=1).fillna(0))

* The distributions don't fit the normal law and the kurtosis is high for many features. We will be able to transform them during feature engineering.
* With the *QuantileTransformer*, some of the output distributions seems cut: this is because the *QuantileTransformer* has difficulties handling preponderent modal classes.
* Althought the *QuantileTransformer* results are sometimes worse than the *Log transformation*, it seems to be globally performing better than the latter.
* We will use the *QuantileTransformer* on our dataset during *Feature Engineering*.

# ***+1 -*** **Conclusion**

This dataset presents encouraging characteristics for modelling:
* It contains a wide palette of distinct values (has a high rate of uniques),
* It has a statisfying fill rate.

However, some features:
* Are highly correlated,
* Do not show a normal distribution,
* Are not formatted correctly to be used by machine learning models.

We have also identified several issues with some of the features and will try to handle these issues during he feature engineering.

The two targets are highly correlated, which means that if we succeed to predict one, we should be able to easily predict the other.

Read the next part of the projet at the following address:

https://colab.research.google.com/drive/1xS0aslIHaJHpGaC1XozQCkEKbhc6uCAC?usp=sharing